In [2]:
import requests
from dotenv import load_dotenv
import os
import re

load_dotenv()

qwen = False
if qwen:
    url = "https://qwen3.chatllm.aiengines.ir/v1/chat/completions"
    model = "Qwen/Qwen3-4B-Instruct-2507"
    headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('LLM_AS_RERANKER_PASS')}"}
else:
    url = "http://192.168.130.206:4001/v1/chat/completions"
    model = "google/gemma-3-27b-it"
    headers = {"Content-Type": "application/json"}

instruction = """
You are a helpful assistant that help me to find that the text is relevant to the question or not.
You are given a question and a text.
You must evaluate the text based on the question and return "1" if the text is relevant to the question and "0" if the text is not relevant to the question.
 
be carefull, I have chosen the text randomly from my dataset so the text must answer the question independently.
You must return the result in the following format:
{{"result": "1" or "0"}}
"""

question = "چرا خورشید اینقدر داغ است؟"
texts = [
            "سیاراتی که در مدار نزدیک به ستاره های کوتوله سرخ قرار دارند، به دلیل نزدیکی به ستاره مادر، تحت تابش تشعشعات شدید قرار می گیرند. این تابش می تواند شرایط زیست محیطی را به شدت تحت تأثیر قرار دهد و ممکن است تنها مکان هایی که حیات در آنجا امکان وجود دارد، زیر لایه های ضخیم یخ باشد. این شرایط می تواند مانع از شکل گیری و تکامل حیات در سطح سیاره شود.",
            "کتاب تابستان به دلیل داستان جذاب و توصیف‌های زیبا از طبیعت و زندگی، توجه تمام علاقه‌مندان به ادبیات داستانی را به خود جلب می‌کند. این کتاب نه تنها احساسات عمیق انسانی را به تصویر می‌کشد بلکه خواننده را به دنیای خاطرات شیرین تابستان‌های کودکی می‌برد.",
            "حضرت ادریس علیه السلام به عنوان منشاء و معلم بسیاری از علوم شناخته می‌شود. او به عنوان یکی از قدیمی‌ترین پیشوایان علم، افکار بشر را به سمت استدلال و دقت در بحث سوق داده است. همچنین، او اولین کسی است که علم نجوم را به الهام الهی استخراج کرده و زمین را به چهار ربع تقسیم نموده است. در دعای روز اول ماه رجب نیز به علم ادریس اشاره شده است.",
            "ستاره‌های کوتوله سرخ معمولاً به صورت دوره‌ای شعله‌هایی از پرتوهای ماورا بنفش و اشعه X ساطع می‌کنند که می‌تواند اتمسفر سیارات اطراف را از بین ببرد و احتمال تشکیل حیات را کاهش دهد. اما ستاره Ross 128 به عنوان یک ستاره آرام شناخته می‌شود و این ویژگی باعث می‌شود که شرایط بهتری برای تشکیل حیات در سیاره Ross 128b فراهم شود.",
            "پوست کودکان به دلیل عدم تکامل کامل ملانوسیت‌ها، سیستم عروقی پوستی و توانایی تولید عرق حساس است. ملانوسیت‌ها که مسئول تولید ملانین هستند، از پوست در برابر اشعه ماورای بنفش محافظت می‌کنند. همچنین، سیستم عروقی پوستی در کودکان هنوز به طور کامل توسعه نیافته و این امر می‌تواند منجر به آسیب‌پذیری بیشتر پوست شود. علاوه بر این، پوست کودکان نمی‌تواند به اندازه کافی عرق تولید کند، که باعث می‌شود رطوبت پوست کاهش یابد. به همین دلیل، پوست کودکان به ویژه نوزادان به نسبت وزن بدن در معرض آسیب بیشتری قرار دارد.",
            "نزول این آیه به واکنش‌های معاصرین پیامبر اسلام، به ویژه ابوجهل و دیگر مخالفان، اشاره دارد که به دلیل عدم درک صحیح از معانی عمیق آیات و قدرت خداوند، به تمسخر و انکار آن می‌پرداختند. این آیه به نوعی به آنها پاسخ می‌دهد و نشان می‌دهد که حتی در آتش، درختی وجود دارد که فراتر از تصور آنهاست. این واکنش‌ها نشان‌دهنده چالش‌های اعتقادی و فکری در آن زمان بود.",
            "شرایط محیطی می‌تواند به عنوان فیلتر عمل کند زیرا عوامل متعددی مانند مقدار و نوع کالری، دما، اتمسفر، آب، خشکی، آفتاب، و بلایای طبیعی مانند آتشفشان و زلزله بر روی موجودات زنده تأثیر می‌گذارد. این عوامل می‌توانند موجودات را به چالش بکشند و تنها آن‌هایی که توانایی سازگاری با این شرایط را دارند، زنده می‌مانند و به نسل‌های بعدی منتقل می‌شوند.",
            "خشکی پوست ممکن است موقتی یا فصلی باشد. به عنوان مثال، در فصل زمستان به دلیل هوای سرد و خشک، بسیاری از افراد دچار خشکی پوست می‌شوند. در مقابل، در فصل‌های گرم و مرطوب، ممکن است این مشکل کاهش یابد. با این حال، برخی افراد ممکن است به طور دائمی با خشکی پوست مواجه باشند که نیاز به مراقبت و درمان مداوم دارد.",
            "سحابی خرچنگ دریایی، که با نام NGC 6357 شناخته می‌شود، به دلیل وجود ستاره‌های غیرمعمول روشن و عظیم در آن، به عنوان یک مکان مهم در کهکشان معرفی می‌شود. این سحابی همچنین خوشۀ ستاره‌ای باز Pismis 24 را در نزدیکی مرکز خود دارد که نشان‌دهنده فعالیت‌های شدید ستاره‌زایی در این ناحیه است. درخشش آبی در نزدیکی منطقه تشکیل ستاره داخلی ناشی از انتشار گاز هیدروژن یونیزه است که به جذابیت این سحابی افزوده است.",
            "سحابی خرچنگ ده سال نوری وسعت دارد و در مرکز آن یک تپ اختر قرار دارد. این تپ اختر به سنگینی خورشید اما به اندازه یک شهر کوچک است و ثانیه‌ای سی بار به دور خود می‌چرخد. همچنین، سحابی خرچنگ با سرعتی حدود 10000 کیلومتر بر ثانیه منبسط می‌شود و انتظار می‌رود که در چند هزار سال آینده به تدریج کم‌فروغ‌تر شده و سرانجام ناپدید گردد.",
            "وجود یک اقیانوس زیر سطحی در قمر اروپا می تواند شرایط لازم برای زندگی موجودات میکروسکوپی را فراهم کند. این اقیانوس می تواند شامل مواد مغذی و حرارت لازم برای حیات باشد. با توجه به اینکه بخار آب فوران شده از سطح اروپا ممکن است به این اقیانوس مرتبط باشد، بررسی های آینده می تواند به دانشمندان کمک کند تا پتانسیل اروپا برای تبدیل شدن به یک محل قابل سکونت را بدون نیاز به حفاری لایه یخ بررسی کنند.",
            "چگالش بوز-اینشتین حالتی از ماده است که در دماهای بسیار پایین ایجاد می‌شود و در آن اتم‌ها رفتار موجی خود را نشان می‌دهند. در این حالت، قوانین فیزیک کلاسیک به کنار می‌روند و فیزیک کوانتومی حاکم می‌شود. اتم‌ها در این حالت به گونه‌ای حرکت می‌کنند که انگار بر روی یکدیگر سوار هستند و این رفتار تنها در دماهای بسیار پایین قابل مشاهده است.",
            "در سال 2012، انجمن سلطنتی شیمی مسابقه‌ای را برای یافتن بهترین توضیح برای اثر امپمبا برگزار کرد. برنده این مسابقه نظریه‌ای را ارائه داد که علت این پدیده را 'ابرسرد شدن' می‌دانست. این نشان می‌دهد که این موضوع همچنان مورد توجه محققان و دانشمندان است و تلاش‌ها برای درک بهتر آن ادامه دارد.",
            "داستان کتاب عاشق آتشفشان در قرن هجدهم و در میان آشفتگی‌های دربار ناپلی اتفاق می‌افتد. این رمان به بررسی موضوعاتی چون عشق، تاریخ و روابط اجتماعی می‌پردازد و داستان زندگی سر ویلیام همیلتون و همسرش اِما را روایت می‌کند. همچنین، این داستان به تحولات سیاسی و اجتماعی آن زمان نیز اشاره دارد.",
            "انفجارهای هوایی به دلیل قدرت تخریب بالای خود و نادر بودن برخورد سیارک‌ها، خطرناک‌تر محسوب می‌شوند. در حالی که برخورد سیارک‌های بزرگ به ندرت اتفاق می‌افتد، انفجارهای هوایی می‌توانند به طور ناگهانی و بدون هشدار پیشین رخ دهند. به عنوان مثال، انفجار سیارکی به اندازه یک خانه در سال ۱۳۹۲ در چلیابینسک روسیه منجر به آسیب دیدن بیش از ۱۶۰۰ نفر شد. این نشان می‌دهد که انفجارهای هوایی می‌توانند تأثیرات جدی بر روی جمعیت‌های انسانی داشته باشند.",
            "پرتقال به دلیل خواص ضدعفونی‌کننده و ضد میکروبی که دارد، می‌تواند به درمان مشکلات پوستی کمک کند. به عنوان مثال، شما می‌توانید از پوست پرتقال له شده به عنوان مرهم برای اگزما و ناراحتی‌های پوستی استفاده کنید. این خاصیت به دلیل وجود ترکیبات طبیعی در پوست پرتقال است که به تسکین و بهبود وضعیت پوست کمک می‌کند.",
            "نوسانات درخشندگی ستاره KIC 8462852 به‌طور نامنظم و شدید اتفاق می‌افتند و این الگو با آنچه معمولاً در ستاره‌های دارای سیارات فراخورشیدی مشاهده می‌شود، متفاوت است. در حالی که وجود یک سیاره می‌تواند باعث نوسانات درخشندگی شود، در این مورد، نوسانات به‌قدری پیچیده و غیرقابل پیش‌بینی هستند که فرضیه‌های دیگر مانند وجود ابرهای میان ستاره‌ای، دنباله‌دارها یا حتی اَبَرسازه‌های بیگانگان فضایی نیز مطرح شده‌اند.",
            "پاریس به عنوان یک مقصد گردشگری محبوب به دلیل جاذبه‌های تاریخی، فرهنگی و هنری خود شناخته می‌شود. این شهر با برج ایفل، موزه لوور، کاتدرال نوتردام و خیابان‌های زیبا و پر از زندگی، هر ساله میلیون‌ها گردشگر را به خود جذب می‌کند. همچنین، فرهنگ غنی، غذاهای لذیذ و فضاهای رمانتیک پاریس، تجربه‌ای منحصر به فرد را برای بازدیدکنندگان فراهم می‌آورد. به همین دلیل، پاریس به عنوان 'شهر نور' و 'شهر عشق' در قلب بسیاری از مردم جهان جای دارد."
        ]
        
for text in texts:
    input_message = f"""{{"question": "{question}", "text": "{text}"}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 100
    }

    req = requests.post(url, headers=headers, json=payload)
    print(text)
    print(req.json()['choices'][0]['message']['content'])
    print("--------------------------------")

سیاراتی که در مدار نزدیک به ستاره های کوتوله سرخ قرار دارند، به دلیل نزدیکی به ستاره مادر، تحت تابش تشعشعات شدید قرار می گیرند. این تابش می تواند شرایط زیست محیطی را به شدت تحت تأثیر قرار دهد و ممکن است تنها مکان هایی که حیات در آنجا امکان وجود دارد، زیر لایه های ضخیم یخ باشد. این شرایط می تواند مانع از شکل گیری و تکامل حیات در سطح سیاره شود.
{"result": "0"}
--------------------------------
کتاب تابستان به دلیل داستان جذاب و توصیف‌های زیبا از طبیعت و زندگی، توجه تمام علاقه‌مندان به ادبیات داستانی را به خود جلب می‌کند. این کتاب نه تنها احساسات عمیق انسانی را به تصویر می‌کشد بلکه خواننده را به دنیای خاطرات شیرین تابستان‌های کودکی می‌برد.
{{"result": "0"}}

--------------------------------
حضرت ادریس علیه السلام به عنوان منشاء و معلم بسیاری از علوم شناخته می‌شود. او به عنوان یکی از قدیمی‌ترین پیشوایان علم، افکار بشر را به سمت استدلال و دقت در بحث سوق داده است. همچنین، او اولین کسی است که علم نجوم را به الهام الهی استخراج کرده و زمین را به چهار ربع تقسیم نموده است. در دعای روز اول ماه رجب 

In [ ]:
from datasets import load_dataset

ds = load_dataset("virattt/financial-qa-10K", split="train")
